In [1]:
import numpy as np
import pandas as pd
import plotly.offline as py
import plotly.graph_objs as go

py.init_notebook_mode(connected=True)

## Surface

On commence avec l'équivalent d'un tracé de courbe en 2D à savoir un tracé de surface. Pour cela on définit

* un maillage en (x,y) avec `np.meshgrid` après avoir indiqué le nombre de points désirés en x et en y avec `np.linspace` (100 points dans l'exemple qui suit),
* les valeurs en z de la surface en tout point du maillage (`mz` dans notre exemple)

Il ne reste plus qu'a utiliser le maillage et les valeurs en z pour définir la `Surface` qu'on affiche avec `iplot`.

In [2]:
x = np.linspace(0,9,100)
y = np.linspace(0,3,100)

mx, my = np.meshgrid(x,y)
mz = np.sin(my) * np.cos(mx)

trace = go.Surface(x=mx, y=my, z=mz)
py.iplot([trace], show_link=False)

Malheureusement le résultat ne correspond pas à ce qu'on attend lorsqu'on connait la forme de $\sin(x) \times \cos(y)$, 
chaque bosse doit être symétrique et avoir une base carrée.

### Définir la scène

Le problème vient du fait que par défault Plotly veut faire tenir le résultat dans un cube et donc les axes ne sont pas
normés ! Aussi il faut indiquer que la vision du résultat respecte les proportions à savoir que la boite qui représente la scène du film est proportionnelle aux min et max des données suivant les axes. Pour cela on doit indiquer dans la mise
en page que l'aspect de la  `scene` respecte les données.

On verra par la suite que le nom des axes est aussi défini dans la `scene` du `layout` et non plus directement dans le
`layout`.

In [3]:
layout = go.Layout(scene = {'aspectmode':'data'})
fig = go.Figure(data=[trace], layout=layout)
py.iplot(fig, show_link=False)

## Maillage surfacique en 3D

La `Surface` vue précédemment correspond à une valeur z pour tout point (x,y) du plan. Si on désire afficher une sphère cela ne marche plus. Il faut utiliser `Mesh` qui permet d'afficher n'importe quelle forme 3D avec un ensemble de triangles, ensemble appelé [maillage](https://fr.wikipedia.org/wiki/Maillage).

L'intérêt d'un tel maillage est d'afficher la variation d'une donnée sur une surface complexe. Cela peut être la pression
sur la surface d'un avion par exemple.

Un maillage est défini par 

* ses noeuds avec pour chaque noeud ses coordonnées `x`,`y`,`z`
* ses triangles avec pour chaque triangle les numéros `i`,`j`,`k` des 3 noeuds qui le forme
* la valeur (`intensity`) en tout noeud qui va définir la couleur affichée

Voici un maillage très simple avec 3 triangles :

In [4]:
data = go.Mesh3d(
        #    0  1  2  3  4  5  6  7 (node number)
        x = [0, 0, 1, 1, 0, 0, 1, 1],
        y = [0, 1, 1, 0, 0, 1, 1, 0],
        z = [0, 0, 0, 0, 1, 1, 1, 1],
        i = [0, 0, 5],
        j = [1, 4, 2],
        k = [2, 7, 3],
        #             0    1    2   3   4    5    6    7 
        intensity = [0.1, 0.2, 0.7, 1, 1.1, 1.3, 0.5, 0.6]
    )
py.iplot([data])

On notera que le noeud numéro 6 n'a pas été utilisé.

Bien sûr en pratique on écrit un programme qui génére les coordonnées et la valeur des noeuds de notre maillage ainsi
que la liste des triangles. En fait, en pratique on utilise un programme dédié à la simulation numériqu

## Nuage de points


In [5]:
food = pd.read_excel("https://ciqual.anses.fr/cms/sites/default/files/inline-files/TableCiqual2017_ExcelENG_2017%2011%2017.xls",
                    decimal=',')

In [6]:
food.alim_grp_nom_eng.unique()

array(['starters and dishes', 'fruits, vegetables, legumes and nuts',
       'cereal products', nan, 'meat, egg and fish',
       'milk and milk products', 'beverages', 'sugar and confectionery',
       'ice cream and sorbet', 'fats and oils', 'miscellaneous',
       'baby food'], dtype=object)

In [7]:
stardish = food[food.alim_grp_nom_eng == 'starters and dishes']

In [8]:
trace = go.Scatter3d(
    x = stardish['Protein (g/100g)'], 
    y = stardish['Fat (g/100g)'],
    z = stardish['Sugars (g/100g)'],
    text = stardish['alim_nom_eng'],
    mode = 'markers',
    marker = dict( 
        color = stardish['Calcium (mg/100g)'],
        colorscale = 'Viridis',
        colorbar = {'title':'Calcium<br>(mg/100g)'},
        opacity = 0.8,
        showscale=True),
)

layout2 = layout.copy() 
layout2['scene'].update(xaxis = {'title':'Protein'}, yaxis = {'title':'Fat'}, zaxis = {'title':'Sugar'})
layout2['title'] = 'What is in that food (g/100g)'

fig = go.Figure(data=[trace], layout=layout2)
py.iplot(fig, show_link=False)

## Plus

La page https://plot.ly/python/3d-charts/ montre une collection de graphiques 3D possibles :

<a href='https://plot.ly/python/3d-charts/'><img src='images/3d_charts.png'/></a>

{{ PreviousNext("23 -- Dynamic graphics with Plotly -- Subplots.ipynb", "30 -- Maps with Folium.ipynb")}}